<a href="https://colab.research.google.com/github/monoramasn/Speech_fairness/blob/main/italian_whisper_base_test_modified.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
!pip install git+https://github.com/huggingface/transformers
!pip install librosa
!pip install evaluate>=0.30
!pip install jiwer
!pip install gradio
!pip install tensorflow

  Cloning https://github.com/huggingface/transformers to /tmp/pip-req-build-thxpkdj4
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/transformers /tmp/pip-req-build-thxpkdj4
  Resolved https://github.com/huggingface/transformers to commit 5d36025ca13d05151b7a0c761e90d429c4644a30
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [3]:
import torch
from transformers import AutoFeatureExtractor, WhisperModel
from datasets import load_dataset

In [4]:
import os
import numpy as np

try:
    import tensorflow  # required in Colab to avoid protobuf compatibility issues
except ImportError:
    pass

import torch
import pandas as pd
import torchaudio

from tqdm.notebook import tqdm



In [41]:
#ds = tfds.load('huggingface:multilingual_librispeech/portuguese')

mls = load_dataset("facebook/multilingual_librispeech", "italian", split="test")


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:72: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/datasets/load.py:1429: FutureWarning: The repository for facebook/multilingual_librispeech contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/facebook/multilingual_librispeech
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this dataset from the next maj

Generating train split: 0 examples [00:00, ? examples/s]

Generating train.9h split: 0 examples [00:00, ? examples/s]

Generating train.1h split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

In [ ]:
#voxpopuli_data = load_dataset("facebook/voxpopuli", "cs", split="test")
#column_name = "audio, normalized_text"

Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

In [42]:
mls

Dataset({
    features: ['file', 'audio', 'text', 'speaker_id', 'chapter_id', 'id'],
    num_rows: 1262
})

In [ ]:
#voxpopuli_data

Dataset({
    features: ['audio_id', 'language', 'audio', 'raw_text', 'normalized_text', 'gender', 'speaker_id', 'is_gold_transcript', 'accent'],
    num_rows: 1123
})

In [43]:
!pip install openai-whisper
import whisper
#model = whisper.load_model("base")

In [44]:
model = whisper.load_model("base")

In [45]:
from transformers import WhisperForConditionalGeneration, WhisperFeatureExtractor,WhisperTokenizer
from datasets import load_dataset
import torch
from tqdm import tqdm
from jiwer import wer

In [46]:
#Gender=mls['gender']
Audio=mls['audio']
text=mls['chapter_id']
#Gender=pd.DataFrame(Gender)
Audio=pd.DataFrame(Audio)
text=pd.DataFrame(text)

In [ ]:
#Gender=voxpopuli_data['gender']
#Audio=voxpopuli_data['audio']
#text=voxpopuli_data['normalized_text']
#Gender=pd.DataFrame(Gender)
#Audio=pd.DataFrame(Audio)
#text=pd.DataFrame(text)

In [47]:
text

0
0      529
1      529
2      529
3      529
4      529
...    ...
1257  8842
1258  8842
1259  8842
1260  8842
1261  8842

[1262 rows x 1 columns]

In [48]:
file=pd.concat([text, Audio],axis=1)
file

0                                               path  \
0      529  /root/.cache/huggingface/datasets/downloads/ex...   
1      529  /root/.cache/huggingface/datasets/downloads/ex...   
2      529  /root/.cache/huggingface/datasets/downloads/ex...   
3      529  /root/.cache/huggingface/datasets/downloads/ex...   
4      529  /root/.cache/huggingface/datasets/downloads/ex...   
...    ...                                                ...   
1257  8842  /root/.cache/huggingface/datasets/downloads/ex...   
1258  8842  /root/.cache/huggingface/datasets/downloads/ex...   
1259  8842  /root/.cache/huggingface/datasets/downloads/ex...   
1260  8842  /root/.cache/huggingface/datasets/downloads/ex...   
1261  8842  /root/.cache/huggingface/datasets/downloads/ex...   

                                                  array  sampling_rate  
0     [-0.008880615234375, -0.00830078125, -0.007904...          16000  
1     [-0.012237548828125, -0.015625, -0.02136230468...          16000  
2     [-0.00537109375, 0.004608154296875, -0.0035400...          16000  
3     [-0.010406494140625, -0.008087158203125, -0.00...          16000  
4     [-0.008209228515625, -0.008453369140625, -0.00...          16000  
...                                                 ...            ...  
1257  [-3.0517578125e-05, -3.0517578125e-05, 9.15527...          16000  
1258  [0.0, 6.103515625e-05, 3.0517578125e-05, 6.103...          16000  
1259  [0.000152587890625, 0.000152587890625, 0.00012...          16000  
1260  [6.103515625e-05, 9.1552734375e-05, 0.00012207...          16000  
1261  [-0.000762939453125, -0.000885009765625, -0.00...          16000  

[1262 rows x 4 columns]

In [49]:
#Gender.columns=['Gender']
text.columns=['Transcript']

In [50]:
file=pd.concat([ text, Audio],axis=1)
file

Transcript                                               path  \
0            529  /root/.cache/huggingface/datasets/downloads/ex...   
1            529  /root/.cache/huggingface/datasets/downloads/ex...   
2            529  /root/.cache/huggingface/datasets/downloads/ex...   
3            529  /root/.cache/huggingface/datasets/downloads/ex...   
4            529  /root/.cache/huggingface/datasets/downloads/ex...   
...          ...                                                ...   
1257        8842  /root/.cache/huggingface/datasets/downloads/ex...   
1258        8842  /root/.cache/huggingface/datasets/downloads/ex...   
1259        8842  /root/.cache/huggingface/datasets/downloads/ex...   
1260        8842  /root/.cache/huggingface/datasets/downloads/ex...   
1261        8842  /root/.cache/huggingface/datasets/downloads/ex...   

                                                  array  sampling_rate  
0     [-0.008880615234375, -0.00830078125, -0.007904...          16000  
1     [-0.012237548828125, -0.015625, -0.02136230468...          16000  
2     [-0.00537109375, 0.004608154296875, -0.0035400...          16000  
3     [-0.010406494140625, -0.008087158203125, -0.00...          16000  
4     [-0.008209228515625, -0.008453369140625, -0.00...          16000  
...                                                 ...            ...  
1257  [-3.0517578125e-05, -3.0517578125e-05, 9.15527...          16000  
1258  [0.0, 6.103515625e-05, 3.0517578125e-05, 6.103...          16000  
1259  [0.000152587890625, 0.000152587890625, 0.00012...          16000  
1260  [6.103515625e-05, 9.1552734375e-05, 0.00012207...          16000  
1261  [-0.000762939453125, -0.000885009765625, -0.00...          16000  

[1262 rows x 4 columns]

In [ ]:
#male_samples=file.loc[file['Gender'] == 'male']
#male_samples

NameError: name 'male_samples' is not defined

In [ ]:
#female_samples=file.loc[file['Gender'] == 'female']
#female_samples

Gender                                         Transcript  \
8     female  nejhorší situace je v somálsku súdánu mauretán...   
9     female  v letecké i železniční dopravě vize nula platí...   
10    female  jen tak potvrdíte že před dvaceti lety lidé ne...   
11    female  v této souvislosti bych očekávala že alespoň d...   
13    female  já sama pocházím z regionu severní moravy ze s...   
...      ...                                                ...   
1106  female  díky tomu se mnoho informací dostává k adresát...   
1109  female  podle dostupných informací turecký premiér dal...   
1114  female  veřejné konzultace jsou běžně zveřejňovány pře...   
1117  female  liší se rozsah průvodních dokumentů opět vesmě...   
1118  female  ale vzhledem ke stárnutí populace a dalším výz...   

                                                   path  \
8     /root/.cache/huggingface/datasets/downloads/ex...   
9     /root/.cache/huggingface/datasets/downloads/ex...   
10    /root/.cache/huggingface/datasets/downloads/ex...   
11    /root/.cache/huggingface/datasets/downloads/ex...   
13    /root/.cache/huggingface/datasets/downloads/ex...   
...                                                 ...   
1106  /root/.cache/huggingface/datasets/downloads/ex...   
1109  /root/.cache/huggingface/datasets/downloads/ex...   
1114  /root/.cache/huggingface/datasets/downloads/ex...   
1117  /root/.cache/huggingface/datasets/downloads/ex...   
1118  /root/.cache/huggingface/datasets/downloads/ex...   

                                                  array  sampling_rate  
8     [-0.001007080078125, -0.001922607421875, -0.00...          16000  
9     [0.001800537109375, 0.0030517578125, 0.0003356...          16000  
10    [-0.001007080078125, 0.0009765625, -0.00057983...          16000  
11    [-0.000518798828125, -0.0020751953125, -0.0010...          16000  
13    [-0.000457763671875, 0.00201416015625, 0.00283...          16000  
...                                                 ...            ...  
1106  [-0.000244140625, -9.1552734375e-05, 0.0009155...          16000  
1109  [-0.00506591796875, -0.008453369140625, -0.003...          16000  
1114  [0.001251220703125, 0.00177001953125, -0.00122...          16000  
1117  [0.00396728515625, 0.003875732421875, 0.005584...          16000  
1118  [-0.00335693359375, -0.01141357421875, 0.00012...          16000  

[374 rows x 5 columns]

In [51]:
def transcribe_audio(file_path):
    result = model.transcribe(file_path, language="italian")
    return result["text"]

In [53]:
def calculate_wer(ground_truths, hypotheses):
    return wer(ground_truths, hypotheses)

In [54]:
from jiwer import wer
from collections import Counter

def calculate_precision_recall_f1(ground_truth, hypothesis):
    ground_truth_words = set(ground_truth.split())
    hypothesis_words = set(hypothesis.split())

    true_positives = ground_truth_words.intersection(hypothesis_words)
    false_positives = hypothesis_words - ground_truth_words
    false_negatives = ground_truth_words - hypothesis_words

    precision = len(true_positives) / (len(true_positives) + len(false_positives)) if true_positives or false_positives else 0
    recall = len(true_positives) / (len(true_positives) + len(false_negatives)) if true_positives or false_negatives else 0
    f1_score = 2 * (precision * recall) / (precision + recall) if precision + recall else 0

    return precision, recall, f1_score

In [55]:

total_wer = 0
total_precision = 0
total_recall = 0
total_f1 = 0
count = 0
#chapter_id = normalized_text

for sample in mls:
    audio_file_path = sample['audio']['path']
    ground_truth_text = sample['text']

    # Transcribe the audio
    transcription = transcribe_audio(audio_file_path)


  # Compute metrics
    sample_wer = calculate_wer(ground_truth_text, transcription)
    precision, recall, f1_score = calculate_precision_recall_f1(ground_truth_text, transcription)

    total_wer += sample_wer
    total_precision += precision
    total_recall += recall
    total_f1 += f1_score
    count += 1
    print(f"Processed {count} files, WER: {sample_wer}, Precision: {precision}, Recall: {recall}, F1: {f1_score}")

# Calculate average metrics
average_wer = total_wer / count
average_precision = total_precision / count
average_recall = total_recall / count
average_f1 = total_f1 / count

print(f"Average WER: {average_wer}")
print(f"Average Precision: {average_precision}")
print(f"Average Recall: {average_recall}")
print(f"Average F1-Score: {average_f1}")




/usr/local/lib/python3.10/dist-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


Processed 1 files, WER: 0.41025641025641024, Precision: 0.6571428571428571, Recall: 0.6571428571428571, F1: 0.6571428571428571


/usr/local/lib/python3.10/dist-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


Processed 2 files, WER: 0.6216216216216216, Precision: 0.41935483870967744, Recall: 0.37142857142857144, F1: 0.393939393939394


/usr/local/lib/python3.10/dist-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


...

Processed 1260 files, WER: 0.2857142857142857, Precision: 0.6923076923076923, Recall: 0.72, F1: 0.7058823529411765


/usr/local/lib/python3.10/dist-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


Processed 1261 files, WER: 0.5, Precision: 0.5625, Recall: 0.6, F1: 0.5806451612903225


/usr/local/lib/python3.10/dist-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


Processed 1262 files, WER: 0.4594594594594595, Precision: 0.5588235294117647, Recall: 0.5588235294117647, F1: 0.5588235294117647
Average WER: 0.4955060695000508
Average Precision: 0.5428067657577784
Average Recall: 0.5521224707937314
Average F1-Score: 0.5468107650097219


/usr/local/lib/python3.10/dist-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


Processed 1 files, WER: 0.7222222222222222


/usr/local/lib/python3.10/dist-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


Processed 2 files, WER: 0.5555555555555556


/usr/local/lib/python3.10/dist-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


...

Processed 372 files, WER: 0.5217391304347826


/usr/local/lib/python3.10/dist-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


Processed 373 files, WER: 0.7894736842105263


/usr/local/lib/python3.10/dist-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


Processed 374 files, WER: 0.5757575757575758
Average WER: 0.666263036157873
